In [ ]:
%reload_ext autoreload
%autoreload 2
if '__file__' not in globals():
    __file__, __name__ = globals()['__vsc_ipynb_file__'], '__ipynb__'
    import types, sys; sys.modules['__ipynb__'] = types.ModuleType('__ipynb__')
    from IPython.core.magic import register_cell_magic
    @register_cell_magic
    def skip_if(flag, cell): exec(cell, globals())if flag and not eval(flag) else print('Cell skipped...')

import sys, os
if os.path.abspath('.') not in sys.path: sys.path.append(os.path.abspath('.'))

import os, huggingface_hub # !pip install huggingface_hub[hf_transfer]
huggingface_hub.login(token = os.environ.get('HF_TOKEN'), add_to_git_credential=True)

import inspect
from pathlib import Path
from tqdm import tqdm
from glob import glob
import numpy as np; np.set_printoptions(precision=8, suppress=True); np.random.seed(42)

class text_color:
    black,red,green,yellow,blue,magenta,cyan,white,gray = [*range(30,38), 90] # fgclr,  [*range(90,98), ''] # light-fgclr
    bold, italic, underline, strike = 1, 3, 4, 9  # attrs supported on vscode notebook.
    def __init__(self, fg,bg=0,attr=0):
        attr = f'{attr};' if attr > 0 else ''
        bg = f'{bg+10};' if bg > 0 else ''
        self.clr = f'\33[{attr}{bg}{fg}m'

    def __ror__(self, obj): return self.clr + str(obj) + '\33[0m'
    @staticmethod
    def all(): return (text_color(clr) for clr in [*range(30,38), 90])

black,red,green,yellow,blue,magenta,cyan,white,gray = text_color.all()

class cout:
    def __ror__(self, obj): print(f'[{inspect.stack()[1].lineno}] {str(obj)}')
    def __call__(self, *args, **kwds): print(f'[{inspect.stack()[1].lineno+1}]', *args, **kwds)
out = cout()

### load weight

In [ ]:
# https://colab.research.google.com/drive/1uskRfCesambdQrhGp2s5wx6zGwSUR0Sh
# https://huggingface.co/microsoft/Phi-3.5-mini-instruct/blob/main/config.json
# https://github.com/microsoft/Phi-3CookBook
# !pip install -q sentencepiece

import torch, peft, transformers

model_id = "microsoft/Phi-3.5-mini-instruct" # 128k, 7.7GB
model_id = "outputs_unslot/merged-model" # ft.

model = transformers.AutoModelForCausalLM.from_pretrained(
    model_id,
    device_map="auto",
    torch_dtype=torch.bfloat16,
    trust_remote_code=True,
    low_cpu_mem_usage=True,
    attn_implementation="flash_attention_2",
)

# model_id = "outputs_unslot/model/lora"
# model = peft.AutoPeftModelForCausalLM.from_pretrained(
#     model_id, device_map="cuda",
#     torch_dtype="auto",
#     trust_remote_code=True,
#     low_cpu_mem_usage=True,
#     attn_implementation="flash_attention_2")

model.config.use_cache = True
model.eval()
print(model)

tokenizer = transformers.AutoTokenizer.from_pretrained(model_id)


In [182]:
from IPython.display import display, Markdown, clear_output

class CallbackTextStreamer(transformers.TextStreamer):
    def __init__(self, markdown=False, **kwargs):
        super().__init__(**kwargs)
        self.markdown = markdown
        self.ans = ""

    def on_finalized_text(self, text: str, stream_end: bool = False):
        super().on_finalized_text(text, stream_end)
        self.ans += text
        if stream_end:
            self.finally_markdown()

    def finally_markdown(self):
        if self.markdown:
            clear_output(wait=False)
            display(Markdown(self.ans))

def generate(input_text, system_prompt="",max_length=512, stream=True):

    if isinstance(input_text, list):
        messages = input_text
    else:
        if not system_prompt:
            system_prompt = "You are a friendly and helpful assistant"
        messages = [
            { "role": "system", "content": system_prompt,},
            {"role": "user", "content": input_text},
        ]

    streamer = CallbackTextStreamer(tokenizer=tokenizer, skip_prompt=True) if stream else None

    prompt = tokenizer.apply_chat_template(messages,
                                           tokenize=False,
                                           add_generation_prompt=True)

    inputs = tokenizer.encode(prompt, add_special_tokens=True, return_tensors="pt").to("cuda")
    outputs = model.generate(input_ids=inputs.to(model.device),
                             max_new_tokens=max_length,
                             do_sample=True,
                             temperature=0.1,
                             top_k=50,
                             streamer=streamer,
                             )
    # text = ''.join([t for t in streamer])

    text = tokenizer.decode(outputs[0, len(inputs[0]):],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    return text


In [183]:
# reformat answer for better cot training
#
system = """Following is dataset to fine tuning llm with cot concept.
To make more good dataset, reformat assistant's cot answer as numbering. And lastly the answer with leading words 'So the answer: '. Answer the reformatted string only."""

content = '''
{"type": "cot", "messages": [{"role": "user", "content": "Kaylee needs to sell 33 boxes of biscuits. So far, she has sold 12 boxes of lemon biscuits to her aunt, 5 boxes of chocolate biscuits to her mother, and 4 boxes of oatmeal biscuits to a neighbor. How many more boxes of biscuits does Kaylee need to sell? Let's think first. Chain of thought:"}, {"role": "assistant", "content": "To solve this problem, we need to find out how many boxes of biscuits Kaylee has sold so far and then subtract that number from the total number of boxes she needs to sell. We can do this by adding up the number of boxes she has sold and then subtracting that sum from the total number of boxes she needs to sell."}], "source": "open-orca"}
'''
# 33 - (12 + 5 + 4) = 12

content = '''\
user query: "Kaylee needs to sell 33 boxes of biscuits. So far, she has sold 12 boxes of lemon biscuits to her aunt, 5 boxes of chocolate biscuits to her mother, and 4 boxes of oatmeal biscuits to a neighbor. How many more boxes of biscuits does Kaylee need to sell? Let's think first. Chain of thought:"

assistant answer: "To solve this problem, we need to find out how many boxes of biscuits Kaylee has sold so far and then subtract that number from the total number of boxes she needs to sell. We can do this by adding up the number of boxes she has sold and then subtracting that sum from the total number of boxes she needs to sell."
'''
gen = generate(content, system, max_length=512)



So the answer: 16

Here's the breakdown:

1. Kaylee has sold 12 boxes of lemon biscuits.
2. She has sold 5 boxes of chocolate biscuits.
3. She has sold 4 boxes of oatmeal biscuits.
4. Total boxes sold so far: 12 (lemon) + 5 (chocolate) + 4 (oatmeal) = 21 boxes.
5. Kaylee needs to sell a total of 33 boxes.
6. Boxes still needed to be sold: 33 (total) - 21 (sold) = 12 boxes.

Therefore, Kaylee needs to sell 12 more boxes of biscuits.<|end|>


In [ ]:
Markdown( generate('Write a detailed analogy between mathematics and a lighthouse.',
         system_prompt="You are Phi, a small language model trained by Microsoft. Write out your reasoning step-by-step to be sure you get the right answers!",
         max_length=1024))

In [ ]:
generate('Write a short email to Sam Altman giving reasons to open source GPT-4',
         system_prompt="You are Phi-3, a large language model trained by Microsoft. Write out your reasoning step-by-step to be sure you get the right answers!",
         max_length=512, stream=True);

In [ ]:
generate('''```python
def detect_prime(n):
   """
   detect if a number is a prime number or not. return True or False
   """''',
   system_prompt="You are a genius python coder, please think carefully and write the following code:");


In [ ]:
gen = generate('Answer the following question by reasoning step by step. The cafeteria had 23 apples. If they used 20 for lunch, and bought 6 more, how many apple do they have?',
         system_prompt="You are Phi-3, a large language model trained by Microsoft. Write out your reasoning step-by-step to be sure you get the right answers!",
         max_length=512)

In [ ]:
gen = generate("Weng earns $12 an hour for babysitting. Yesterday, she just did 50 minutes of babysitting. How much did she earn?",
         system_prompt="Write out your reasoning step-by-step to be sure you get the right answers!",
         max_length=512)

### function call

In [ ]:
import datasets, re, json

ds_test = datasets.load_dataset("json", data_files="xlam-dataset-60k-qwen2-test.jsonl")['train']

system_prompt = "Write out your reasoning step-by-step to be sure you get the right answers!"


for i, sample in enumerate(ds_test):
    message = sample["messages"]
    user_content = message[0]['content']
    # message.insert(0, dict(role='system', content=system_prompt))

    ans = message[-1]["content"]
    gen = generate(message[:-1], stream=False)
    gen = gen.replace('```json', '').replace('```', '')

    true,false = True,False
    gen = json.dumps(eval(gen), indent=3)
    ans = json.dumps(eval(ans), indent=3)

    if gen != ans:
        # print(f'{i}.query:', user_content[-200:]|gray)
        print('gen:', gen|red)
        print('ans:', ans|green)

### from https://deepgram.com/learn/chain-of-thought-prompting-guide

In [184]:
prompts = [
("Roger has 5 tennis balls. He buys 2 more cans of tennis balls. Each can has 3 tennis balls. How many tennis balls does he have now?", 11),
("Yes or no: Would a pear sink in water?",None),
("How would you bring me something that isn’t a fruit?",None),
("How many keystrokes are needed to type the numbers from 1 to 500?", 1392),
("The concert was scheduled to be on 06/01/1943, but was delayed by one day to today. What is the date 10 days ago in MM/DD/YYYY?", "05/23/1943"),
("Take the last letters of the words in 'Lady Gaga' and concatenate them.", 'ya'),
("Sammy wanted to go to where the people were. Where might he go?",None),
("Is the following sentence plausible? 'Joao Moutinho caught the screen pass in the NFC championship.'", 'not plausible'),
("A coin is heads up. Maybelle flips the coin. Shalonda does not flip the coin. Is the coin still heads up?", "No"),
('Answer the following question by reasoning step by step. The cafeteria had 23 apples. If they used 20 for lunch, and bought 6 more, how many apple do they have?', 9)
]

line = 2
generate(prompts[line-2][0],
         system_prompt="Write out your reasoning step-by-step to be sure you get the right answers!",
         max_length=512)

if prompts[line-2][1]:
    print('answer:', prompts[line-2][1])

Roger starts with 5 tennis balls.

He buys 2 more cans, and each can has 3 tennis balls. So, the number of tennis balls in the cans is:
2 cans * 3 tennis balls per can = 6 tennis balls

Now, we add the tennis balls he already had to the ones he bought:
5 tennis balls + 6 tennis balls = 11 tennis balls

Roger now has a total of 11 tennis balls.<|end|>
answer: 11


In [ ]:
react_prompt = """\
Assistant is a large language model trained by Microsoft.

Assistant is designed to be able to assist with a wide range of tasks, from answering simple questions to providing in-depth explanations and discussions on a wide range of topics. As a language model, Assistant is able to generate human-like text based on the input it receives, allowing it to engage in natural-sounding conversations and provide responses that are coherent and relevant to the topic at hand.

Assistant is constantly learning and improving, and its capabilities are constantly evolving. It is able to process and understand large amounts of text, and can use this knowledge to provide accurate and informative responses to a wide range of questions. Additionally, Assistant is able to generate its own text based on the input it receives, allowing it to engage in discussions and provide explanations and descriptions on a wide range of topics.

Overall, Assistant is a powerful tool that can help with a wide range of tasks and provide valuable insights and information on a wide range of topics. Whether you need help with a specific question or just want to have a conversation about a particular topic, Assistant is here to assist.

TOOLS:
------

Assistant has access to the following tools:

wikipedia_search - searches the wikipedia database for the answer\n
web_search - searches the web for the answer\n
calculator - calculates the answer to the question\n
weather_api - gets the weather for the location\n


To use a tool, please use the following format:

```
Thought: Do I need to use a tool? Yes
Action: the action to take, should be one of [wikipedia_search, web_search, calculator, weather_api]
Action Input: the input to the action
Observation: the result of the action
```

When you have a response to say to the Human, or if you do not need to use a tool, you MUST use the format:

```
Thought: Do I need to use a tool? No
Final Answer: [your response here]
```

Begin!


New input: {query}
""" #{agent_scratchpad}


In [ ]:
gen = generate(react_prompt.format(query="What is the latest AI news today?"), max_length=512)

In [ ]:
generate(react_prompt.format(query="오늘 날씨 어때?"), max_length=512)

In [ ]:
generate("사과와 귤중 어떤게 더 맛있어?", max_length=1024)

# ollama

In [ ]:
import openai
from IPython.display import display, Markdown
from multimethod import multimethod
_ollama = openai.OpenAI(base_url='http://localhost:11434/v1')

ollama_model_id = 'phi3.5:3.8b-mini-instruct-q8_0'
ollama_model_id = 'jjkim76/phi3.5-fc:Q8_0'

def generate(input_text, system_prompt=None, max_length=1024):
    if system_prompt is None:
        system_prompt = """Write out your reasoning step-by-step to be sure you get the right answers!"""

    messages = input_text
    if not isinstance(messages, list):
        messages = [dict(role="system", content=system_prompt), dict(role="user", content=input_text)]

    response = _ollama.chat.completions.create(
        model=ollama_model_id,
        messages=messages,
        temperature = 0.01, top_p = 0.01,
        max_tokens=max_length,
        # do_sample=True, temperature=0.1, top_k=50,
    )
    text = response.choices[0].message.content
    # print(input_text[-200:]|gray)
    # display(Markdown(text))
    return text


